## PROBLEM 5 (40 points)
### The ***value*** of an actor is the sum of the rental revenues of *all* the films that the actor was in, based on the films' rental payments. Do the following:
- ### Calculate the sum of the values of *all* the actors in the film(s) that have the *lowest* rental count.
- ### Calculate the sum of the values of the *most popular* actor(s) in the film(s) that have the *highest* rental count. Popularity is a measure of the number of films an actor is in. There can be ties of who's the most popular.
- ### Display in a dataframe the two sums, each formatted as monetary amounts.

In [ ]:
from data201 import db_connection, df_query
conn = db_connection(config_file='sakila.ini')

#### Rental counts of the films.

In [ ]:
df_query(conn,
    """
    WITH
		film_rental_counts AS
		(
            SELECT film_id,
            	   COUNT(rental_id) AS rental_count
            FROM film
            JOIN inventory USING (film_id)
            JOIN rental USING (inventory_id)
            GROUP BY film_id
            ORDER BY rental_count
    	)	
    SELECT * FROM film_rental_counts
    """
)

#### Minimum and maximum film rental counts.

In [ ]:
df_query(conn,
    """
    WITH
		film_rental_counts AS
		(
            SELECT film_id,
            	   COUNT(rental_id) AS rental_count
            FROM film
            JOIN inventory USING (film_id)
            JOIN rental USING (inventory_id)
            GROUP BY film_id
            ORDER BY rental_count
    	),
        min_max_rental_counts AS
        (
    		SELECT MIN(rental_count) AS min_rental_count,
                   MAX(rental_count) AS max_rental_count
            FROM film_rental_counts
        )	
    -- SELECT * FROM film_rental_counts
    SELECT * FROM min_max_rental_counts
    """
)

#### The least rented films.

In [ ]:
df_query(conn,
    """
    WITH
		film_rental_counts AS
		(
            SELECT film_id,
            	   COUNT(rental_id) AS rental_count
            FROM film
            JOIN inventory USING (film_id)
            JOIN rental USING (inventory_id)
            GROUP BY film_id
            ORDER BY rental_count
    	),
        min_max_rental_counts AS
        (
    		SELECT MIN(rental_count) AS min_rental_count,
                   MAX(rental_count) AS max_rental_count
            FROM film_rental_counts
        ),
        least_rented_films AS
        (
            SELECT rental_count,
                   film_id AS least_rented_film_id
            FROM film_rental_counts
            JOIN min_max_rental_counts
            WHERE rental_count = min_rental_count
        )
    -- SELECT * FROM film_rental_counts
    -- SELECT * FROM min_max_rental_counts
    SELECT * FROM least_rented_films
    """
)

#### The most rented films.

In [ ]:
df_query(conn,
    """
    WITH
		film_rental_counts AS
		(
            SELECT film_id,
            	   COUNT(rental_id) AS rental_count
            FROM film
            JOIN inventory USING (film_id)
            LEFT OUTER JOIN rental USING (inventory_id)
            GROUP BY film_id
            ORDER BY rental_count
    	),
        min_max_rental_counts AS
        (
    		SELECT MIN(rental_count) AS min_rental_count,
                   MAX(rental_count) AS max_rental_count
            FROM film_rental_counts
        ),
        least_rented_films AS
        (
            SELECT rental_count,
                   film_id AS least_rented_film_id
            FROM film_rental_counts
            JOIN min_max_rental_counts
            WHERE rental_count = min_rental_count
        ),
        most_rented_films AS
        (
            SELECT rental_count,
                   film_id AS most_rented_film_id
            FROM film_rental_counts
            JOIN min_max_rental_counts
            WHERE rental_count = max_rental_count
        )
    -- SELECT * FROM film_rental_counts
    -- SELECT * FROM min_max_rental_counts
    -- SELECT * FROM least_rented_films
    SELECT * FROM most_rented_films
    """
)

#### Actors of the least rented films.

In [ ]:
df_query(conn,
    """
    WITH
		film_rental_counts AS
		(
            SELECT film_id,
            	   COUNT(rental_id) AS rental_count
            FROM film
            JOIN inventory USING (film_id)
            JOIN rental USING (inventory_id)
            GROUP BY film_id
            ORDER BY rental_count
    	),
        min_max_rental_counts AS
        (
    		SELECT MIN(rental_count) AS min_rental_count,
                   MAX(rental_count) AS max_rental_count
            FROM film_rental_counts
        ),
        least_rented_films AS
        (
            SELECT rental_count,
                   film_id AS least_rented_film_id
            FROM film_rental_counts
            JOIN min_max_rental_counts
            WHERE rental_count = min_rental_count
        ),
        most_rented_films AS
        (
            SELECT rental_count,
                   film_id AS most_rented_film_id
            FROM film_rental_counts
            JOIN min_max_rental_counts
            WHERE rental_count = max_rental_count
        ),
        actors_of_least_rented_films AS
        (
            SELECT DISTINCT actor_id
            FROM film_actor 
            JOIN least_rented_films
            WHERE film_id = least_rented_film_id
        )
    -- SELECT * FROM film_rental_counts
    -- SELECT * FROM min_max_rental_counts
    -- SELECT * FROM least_rented_films
    -- SELECT * FROM most_rented_films
    SELECT * FROM actors_of_least_rented_films ORDER BY actor_id
    """
)

#### Actors of the most rented films.

In [ ]:
df_query(conn,
    """
    WITH
		film_rental_counts AS
		(
            SELECT film_id,
            	   COUNT(rental_id) AS rental_count
            FROM film
            JOIN inventory USING (film_id)
            JOIN rental USING (inventory_id)
            GROUP BY film_id
            ORDER BY rental_count
    	),
        min_max_rental_counts AS
        (
    		SELECT MIN(rental_count) AS min_rental_count,
                   MAX(rental_count) AS max_rental_count
            FROM film_rental_counts
        ),
        least_rented_films AS
        (
            SELECT rental_count,
                   film_id AS least_rented_film_id
            FROM film_rental_counts
            JOIN min_max_rental_counts
            WHERE rental_count = min_rental_count
        ),
        most_rented_films AS
        (
            SELECT rental_count,
                   film_id AS most_rented_film_id
            FROM film_rental_counts
            JOIN min_max_rental_counts
            WHERE rental_count = max_rental_count
        ),
        actors_of_least_rented_films AS
        (
            SELECT DISTINCT actor_id
            FROM film_actor 
            JOIN least_rented_films
            WHERE film_id = least_rented_film_id
        ),
        actors_of_most_rented_films AS
        (
            SELECT DISTINCT actor_id
            FROM film_actor 
            JOIN most_rented_films
            WHERE film_id = most_rented_film_id
        )
    -- SELECT * FROM film_rental_counts
    -- SELECT * FROM min_max_rental_counts
    -- SELECT * FROM least_rented_films
    -- SELECT * FROM most_rented_films
    -- SELECT * FROM actors_of_least_rented_films
    SELECT * FROM actors_of_most_rented_films
    """
)

#### Film counts of the actors of the most rented films.

In [ ]:
df_query(conn,
    """
    WITH
		film_rental_counts AS
		(
            SELECT film_id,
            	   COUNT(rental_id) AS rental_count
            FROM film
            JOIN inventory USING (film_id)
            JOIN rental USING (inventory_id)
            GROUP BY film_id
            ORDER BY rental_count
    	),
        min_max_rental_counts AS
        (
    		SELECT MIN(rental_count) AS min_rental_count,
                   MAX(rental_count) AS max_rental_count
            FROM film_rental_counts
        ),
        least_rented_films AS
        (
            SELECT rental_count,
                   film_id AS least_rented_film_id
            FROM film_rental_counts
            JOIN min_max_rental_counts
            WHERE rental_count = min_rental_count
        ),
        most_rented_films AS
        (
            SELECT rental_count,
                   film_id AS most_rented_film_id
            FROM film_rental_counts
            JOIN min_max_rental_counts
            WHERE rental_count = max_rental_count
        ),
        actors_of_least_rented_films AS
        (
            SELECT DISTINCT actor_id
            FROM film_actor 
            JOIN least_rented_films
            WHERE film_id = least_rented_film_id
        ),
        actors_of_most_rented_films AS
        (
            SELECT DISTINCT actor_id
            FROM film_actor 
            JOIN most_rented_films
            WHERE film_id = most_rented_film_id
        ),
        film_counts_of_actors_of_most_rented_films AS
        (
            SELECT actor_id, 
                   COUNT(film_id) AS film_count
            FROM actors_of_most_rented_films
            JOIN film_actor USING (actor_id)
            GROUP BY actor_id
            ORDER BY film_count DESC
        )
    -- SELECT * FROM film_rental_counts
    -- SELECT * FROM min_max_rental_counts
    -- SELECT * FROM least_rented_films
    -- SELECT * FROM most_rented_films
    -- SELECT * FROM actors_of_least_rented_films
    -- SELECT * FROM actors_of_most_rented_films
    SELECT * FROM film_counts_of_actors_of_most_rented_films
    """
)

#### The most popular actor(s) of the most rented films.

In [ ]:
df_query(conn,
    """
    WITH
		film_rental_counts AS
		(
            SELECT film_id,
            	   COUNT(rental_id) AS rental_count
            FROM film
            JOIN inventory USING (film_id)
            JOIN rental USING (inventory_id)
            GROUP BY film_id
            ORDER BY rental_count
    	),
        min_max_rental_counts AS
        (
    		SELECT MIN(rental_count) AS min_rental_count,
                   MAX(rental_count) AS max_rental_count
            FROM film_rental_counts
        ),
        least_rented_films AS
        (
            SELECT rental_count,
                   film_id AS least_rented_film_id
            FROM film_rental_counts
            JOIN min_max_rental_counts
            WHERE rental_count = min_rental_count
        ),
        most_rented_films AS
        (
            SELECT rental_count,
                   film_id AS most_rented_film_id
            FROM film_rental_counts
            JOIN min_max_rental_counts
            WHERE rental_count = max_rental_count
        ),
        actors_of_least_rented_films AS
        (
            SELECT DISTINCT actor_id
            FROM film_actor 
            JOIN least_rented_films
            WHERE film_id = least_rented_film_id
        ),
        actors_of_most_rented_films AS
        (
            SELECT DISTINCT actor_id
            FROM film_actor 
            JOIN most_rented_films
            WHERE film_id = most_rented_film_id
        ),
        film_counts_of_actors_of_most_rented_films AS
        (
            SELECT actor_id, 
                   COUNT(film_id) AS film_count
            FROM actors_of_most_rented_films
            JOIN film_actor USING (actor_id)
            GROUP BY actor_id
            ORDER BY film_count DESC
        ),
        most_popular_actors_of_most_rented_films AS
        (
            SELECT actor_id
            FROM film_counts_of_actors_of_most_rented_films
            WHERE film_count = (
                SELECT MAX(film_count)
                FROM film_counts_of_actors_of_most_rented_films
            )
        )
    -- SELECT * FROM film_rental_counts
    -- SELECT * FROM min_max_rental_counts
    -- SELECT * FROM least_rented_films
    -- SELECT * FROM most_rented_films
    -- SELECT * FROM actors_of_least_rented_films
    -- SELECT * FROM actors_of_most_rented_films
    -- SELECT * FROM film_counts_of_actors_of_most_rented_films
    SELECT * FROM most_popular_actors_of_most_rented_films
    """
)

#### All films of the most popular actor(s) of the most rented films.

In [ ]:
df_query(conn,
    """
    WITH
		film_rental_counts AS
		(
            SELECT film_id,
            	   COUNT(rental_id) AS rental_count
            FROM film
            JOIN inventory USING (film_id)
            LEFT OUTER JOIN rental USING (inventory_id)
            GROUP BY film_id
            ORDER BY rental_count
    	),
        min_max_rental_counts AS
        (
    		SELECT MIN(rental_count) AS min_rental_count,
                   MAX(rental_count) AS max_rental_count
            FROM film_rental_counts
        ),
        least_rented_films AS
        (
            SELECT rental_count,
                   film_id AS least_rented_film_id
            FROM film_rental_counts
            JOIN min_max_rental_counts
            WHERE rental_count = min_rental_count
        ),
        most_rented_films AS
        (
            SELECT rental_count,
                   film_id AS most_rented_film_id
            FROM film_rental_counts
            JOIN min_max_rental_counts
            WHERE rental_count = max_rental_count
        ),
        actors_of_least_rented_films AS
        (
            SELECT DISTINCT actor_id
            FROM film_actor 
            JOIN least_rented_films
            WHERE film_id = least_rented_film_id
        ),
        actors_of_most_rented_films AS
        (
            SELECT DISTINCT actor_id
            FROM film_actor 
            JOIN most_rented_films
            WHERE film_id = most_rented_film_id
        ),
        film_counts_of_actors_of_most_rented_films AS
        (
            SELECT actor_id, 
                   COUNT(film_id) AS film_count
            FROM actors_of_most_rented_films
            JOIN film_actor USING (actor_id)
            GROUP BY actor_id
            ORDER BY film_count DESC
        ),
        most_popular_actors_of_most_rented_films AS
        (
            SELECT actor_id
            FROM film_counts_of_actors_of_most_rented_films
            WHERE film_count = (
                SELECT MAX(film_count)
                FROM film_counts_of_actors_of_most_rented_films
            )
        ),
        all_films_of_most_popular_actors_of_most_rented_films AS
        (
            SELECT actor_id, film_id
            FROM most_popular_actors_of_most_rented_films
            JOIN film_actor USING (actor_id)
        )
    -- SELECT * FROM film_rental_counts
    -- SELECT * FROM min_max_rental_counts
    -- SELECT * FROM least_rented_films
    -- SELECT * FROM most_rented_films
    -- SELECT * FROM actors_of_least_rented_films
    -- SELECT * FROM actors_of_most_rented_films
    -- SELECT * FROM film_counts_of_actors_of_most_rented_films
    -- SELECT * FROM most_popular_actors_of_most_rented_films
    SELECT * FROM all_films_of_most_popular_actors_of_most_rented_films
    """
)

#### The values of all the actors of the least rented films.

In [ ]:
df_query(conn,
    """
    WITH
		film_rental_counts AS
		(
            SELECT film_id,
            	   COUNT(rental_id) AS rental_count
            FROM film
            JOIN inventory USING (film_id)
            JOIN rental USING (inventory_id)
            GROUP BY film_id
            ORDER BY rental_count
    	),
        min_max_rental_counts AS
        (
    		SELECT MIN(rental_count) AS min_rental_count,
                   MAX(rental_count) AS max_rental_count
            FROM film_rental_counts
        ),
        least_rented_films AS
        (
            SELECT rental_count,
                   film_id AS least_rented_film_id
            FROM film_rental_counts
            JOIN min_max_rental_counts
            WHERE rental_count = min_rental_count
        ),
        most_rented_films AS
        (
            SELECT rental_count,
                   film_id AS most_rented_film_id
            FROM film_rental_counts
            JOIN min_max_rental_counts
            WHERE rental_count = max_rental_count
        ),
        actors_of_least_rented_films AS
        (
            SELECT DISTINCT actor_id
            FROM film_actor 
            JOIN least_rented_films
            WHERE film_id = least_rented_film_id
        ),
        actors_of_most_rented_films AS
        (
            SELECT DISTINCT actor_id
            FROM film_actor 
            JOIN most_rented_films
            WHERE film_id = most_rented_film_id
        ),
        film_counts_of_actors_of_most_rented_films AS
        (
            SELECT actor_id, 
                   COUNT(film_id) AS film_count
            FROM actors_of_most_rented_films
            JOIN film_actor USING (actor_id)
            GROUP BY actor_id
            ORDER BY film_count DESC
        ),
        most_popular_actors_of_most_rented_films AS
        (
            SELECT actor_id
            FROM film_counts_of_actors_of_most_rented_films
            WHERE film_count = (
                SELECT MAX(film_count)
                FROM film_counts_of_actors_of_most_rented_films
            )
        ),
        all_films_of_most_popular_actors_of_most_rented_films AS
        (
            SELECT actor_id, film_id
            FROM most_popular_actors_of_most_rented_films
            JOIN film_actor USING (actor_id)
        ),
        values_of_all_actors_of_least_rented_films AS
        (
            SELECT actor_id, 
                   SUM(amount) AS values_of_all_least_rented_film_actors
            FROM actors_of_least_rented_films
            JOIN film_actor USING (actor_id)
            JOIN film USING (film_id)
            JOIN inventory USING (film_id)
            JOIN rental USING (inventory_id)
            JOIN payment USING (rental_id)
            GROUP BY actor_id
        )
    -- SELECT * FROM film_rental_counts
    -- SELECT * FROM min_max_rental_counts
    -- SELECT * FROM least_rented_films
    -- SELECT * FROM most_rented_films
    -- SELECT * FROM actors_of_least_rented_films
    -- SELECT * FROM actors_of_most_rented_films
    -- SELECT * FROM film_counts_of_actors_of_most_rented_films
    -- SELECT * FROM most_popular_actors_of_most_rented_films
    -- SELECT * FROM all_films_of_most_popular_actors_of_most_rented_films
    SELECT * FROM values_of_all_actors_of_least_rented_films ORDER BY actor_id
    """
)

#### The values of the most popular actors of the most rented films.

In [ ]:
df_query(conn,
    """
    WITH
		film_rental_counts AS
		(
            SELECT film_id,
            	   COUNT(rental_id) AS rental_count
            FROM film
            JOIN inventory USING (film_id)
            JOIN rental USING (inventory_id)
            GROUP BY film_id
            ORDER BY rental_count
    	),
        min_max_rental_counts AS
        (
    		SELECT MIN(rental_count) AS min_rental_count,
                   MAX(rental_count) AS max_rental_count
            FROM film_rental_counts
        ),
        least_rented_films AS
        (
            SELECT rental_count,
                   film_id AS least_rented_film_id
            FROM film_rental_counts
            JOIN min_max_rental_counts
            WHERE rental_count = min_rental_count
        ),
        most_rented_films AS
        (
            SELECT rental_count,
                   film_id AS most_rented_film_id
            FROM film_rental_counts
            JOIN min_max_rental_counts
            WHERE rental_count = max_rental_count
        ),
        actors_of_least_rented_films AS
        (
            SELECT DISTINCT actor_id
            FROM film_actor 
            JOIN least_rented_films
            WHERE film_id = least_rented_film_id
        ),
        actors_of_most_rented_films AS
        (
            SELECT DISTINCT actor_id
            FROM film_actor 
            JOIN most_rented_films
            WHERE film_id = most_rented_film_id
        ),
        film_counts_of_actors_of_most_rented_films AS
        (
            SELECT actor_id, 
                   COUNT(film_id) AS film_count
            FROM actors_of_most_rented_films
            JOIN film_actor USING (actor_id)
            GROUP BY actor_id
            ORDER BY film_count DESC
        ),
        most_popular_actors_of_most_rented_films AS
        (
            SELECT actor_id
            FROM film_counts_of_actors_of_most_rented_films
            WHERE film_count = (
                SELECT MAX(film_count)
                FROM film_counts_of_actors_of_most_rented_films
            )
        ),
        all_films_of_most_popular_actors_of_most_rented_films AS
        (
            SELECT actor_id, film_id
            FROM most_popular_actors_of_most_rented_films
            JOIN film_actor USING (actor_id)
        ),
        values_of_all_actors_of_least_rented_films AS
        (
            SELECT actor_id, 
                   SUM(amount) AS values_of_all_least_rented_film_actors
            FROM actors_of_least_rented_films
            JOIN film_actor USING (actor_id)
            JOIN film USING (film_id)
            JOIN inventory USING (film_id)
            JOIN rental USING (inventory_id)
            JOIN payment USING (rental_id)
            GROUP BY actor_id
        ),
        values_of_most_popular_actors_of_most_rented_films AS
        (
            SELECT actor_id,
                   SUM(amount) AS values_of_most_popular_most_rented_film_actors
            FROM most_popular_actors_of_most_rented_films
            JOIN film_actor USING (actor_id)
            JOIN film USING (film_id)
            JOIN inventory USING (film_id)
            JOIN rental USING (inventory_id)
            JOIN payment USING (rental_id)
            GROUP BY actor_id
        )
    -- SELECT * FROM film_rental_counts
    -- SELECT * FROM min_max_rental_counts
    -- SELECT * FROM least_rented_films
    -- SELECT * FROM most_rented_films
    -- SELECT * FROM actors_of_least_rented_films
    -- SELECT * FROM actors_of_most_rented_films
    -- SELECT * FROM film_counts_of_actors_of_most_rented_films
    -- SELECT * FROM most_popular_actors_of_most_rented_films
    -- SELECT * FROM all_films_of_most_popular_actors_of_most_rented_films
    -- SELECT * FROM values_of_all_actors_of_least_rented_films ORDER BY actor_id
    SELECT * FROM values_of_most_popular_actors_of_most_rented_films ORDER BY actor_id
    """
)

#### The total value of all the actors of the least rented films.

In [ ]:
df_query(conn,
    """
    WITH
		film_rental_counts AS
		(
            SELECT film_id,
            	   COUNT(rental_id) AS rental_count
            FROM film
            JOIN inventory USING (film_id)
            JOIN rental USING (inventory_id)
            GROUP BY film_id
            ORDER BY rental_count
    	),
        min_max_rental_counts AS
        (
    		SELECT MIN(rental_count) AS min_rental_count,
                   MAX(rental_count) AS max_rental_count
            FROM film_rental_counts
        ),
        least_rented_films AS
        (
            SELECT rental_count,
                   film_id AS least_rented_film_id
            FROM film_rental_counts
            JOIN min_max_rental_counts
            WHERE rental_count = min_rental_count
        ),
        most_rented_films AS
        (
            SELECT rental_count,
                   film_id AS most_rented_film_id
            FROM film_rental_counts
            JOIN min_max_rental_counts
            WHERE rental_count = max_rental_count
        ),
        actors_of_least_rented_films AS
        (
            SELECT DISTINCT actor_id
            FROM film_actor 
            JOIN least_rented_films
            WHERE film_id = least_rented_film_id
        ),
        actors_of_most_rented_films AS
        (
            SELECT DISTINCT actor_id
            FROM film_actor 
            JOIN most_rented_films
            WHERE film_id = most_rented_film_id
        ),
        film_counts_of_actors_of_most_rented_films AS
        (
            SELECT actor_id, 
                   COUNT(film_id) AS film_count
            FROM actors_of_most_rented_films
            JOIN film_actor USING (actor_id)
            GROUP BY actor_id
            ORDER BY film_count DESC
        ),
        most_popular_actors_of_most_rented_films AS
        (
            SELECT actor_id
            FROM film_counts_of_actors_of_most_rented_films
            WHERE film_count = (
                SELECT MAX(film_count)
                FROM film_counts_of_actors_of_most_rented_films
            )
        ),
        all_films_of_most_popular_actors_of_most_rented_films AS
        (
            SELECT actor_id, film_id
            FROM most_popular_actors_of_most_rented_films
            JOIN film_actor USING (actor_id)
        ),
        values_of_all_actors_of_least_rented_films AS
        (
            SELECT actor_id, 
                   SUM(amount) AS values_of_all_least_rented_film_actors
            FROM actors_of_least_rented_films
            JOIN film_actor USING (actor_id)
            JOIN film USING (film_id)
            JOIN inventory USING (film_id)
            JOIN rental USING (inventory_id)
            JOIN payment USING (rental_id)
            GROUP BY actor_id
        ),
        values_of_most_popular_actors_of_most_rented_films AS
        (
            SELECT actor_id,
                   SUM(amount) AS values_of_most_popular_most_rented_film_actors
            FROM most_popular_actors_of_most_rented_films
            JOIN film_actor USING (actor_id)
            JOIN film USING (film_id)
            JOIN inventory USING (film_id)
            JOIN rental USING (inventory_id)
            JOIN payment USING (rental_id)
            GROUP BY actor_id
        ),
        total_values_of_all_least_rented_film_actors AS
        (
            SELECT SUM(values_of_all_least_rented_film_actors) 
                      AS total_value_of_all_least_rented_film_actors
            FROM values_of_all_actors_of_least_rented_films
        )
    -- SELECT * FROM film_rental_counts
    -- SELECT * FROM min_max_rental_counts
    -- SELECT * FROM least_rented_films
    -- SELECT * FROM most_rented_films
    -- SELECT * FROM actors_of_least_rented_films
    -- SELECT * FROM actors_of_most_rented_films
    -- SELECT * FROM film_counts_of_actors_of_most_rented_films
    -- SELECT * FROM most_popular_actors_of_most_rented_films
    -- SELECT * FROM all_films_of_most_popular_actors_of_most_rented_films
    -- SELECT * FROM values_of_all_actors_of_least_rented_films ORDER BY actor_id
    SELECT * FROM total_values_of_all_least_rented_film_actors
    """
)

#### The total value of the most popular actors of the most rented films.

In [ ]:
df_query(conn,
    """
    WITH
		film_rental_counts AS
		(
            SELECT film_id,
            	   COUNT(rental_id) AS rental_count
            FROM film
            JOIN inventory USING (film_id)
            JOIN rental USING (inventory_id)
            GROUP BY film_id
            ORDER BY rental_count
    	),
        min_max_rental_counts AS
        (
    		SELECT MIN(rental_count) AS min_rental_count,
                   MAX(rental_count) AS max_rental_count
            FROM film_rental_counts
        ),
        least_rented_films AS
        (
            SELECT rental_count,
                   film_id AS least_rented_film_id
            FROM film_rental_counts
            JOIN min_max_rental_counts
            WHERE rental_count = min_rental_count
        ),
        most_rented_films AS
        (
            SELECT rental_count,
                   film_id AS most_rented_film_id
            FROM film_rental_counts
            JOIN min_max_rental_counts
            WHERE rental_count = max_rental_count
        ),
        actors_of_least_rented_films AS
        (
            SELECT DISTINCT actor_id
            FROM film_actor 
            JOIN least_rented_films
            WHERE film_id = least_rented_film_id
        ),
        actors_of_most_rented_films AS
        (
            SELECT DISTINCT actor_id
            FROM film_actor 
            JOIN most_rented_films
            WHERE film_id = most_rented_film_id
        ),
        film_counts_of_actors_of_most_rented_films AS
        (
            SELECT actor_id, 
                   COUNT(film_id) AS film_count
            FROM actors_of_most_rented_films
            JOIN film_actor USING (actor_id)
            GROUP BY actor_id
            ORDER BY film_count DESC
        ),
        most_popular_actors_of_most_rented_films AS
        (
            SELECT actor_id
            FROM film_counts_of_actors_of_most_rented_films
            WHERE film_count = (
                SELECT MAX(film_count)
                FROM film_counts_of_actors_of_most_rented_films
            )
        ),
        all_films_of_most_popular_actors_of_most_rented_films AS
        (
            SELECT actor_id, film_id
            FROM most_popular_actors_of_most_rented_films
            JOIN film_actor USING (actor_id)
        ),
        values_of_all_actors_of_least_rented_films AS
        (
            SELECT actor_id, 
                   SUM(amount) AS values_of_all_least_rented_film_actors
            FROM actors_of_least_rented_films
            JOIN film_actor USING (actor_id)
            JOIN film USING (film_id)
            JOIN inventory USING (film_id)
            JOIN rental USING (inventory_id)
            JOIN payment USING (rental_id)
            GROUP BY actor_id
        ),
        values_of_most_popular_actors_of_most_rented_films AS
        (
            SELECT actor_id,
                   SUM(amount) AS values_of_most_popular_most_rented_film_actors
            FROM most_popular_actors_of_most_rented_films
            JOIN film_actor USING (actor_id)
            JOIN film USING (film_id)
            JOIN inventory USING (film_id)
            JOIN rental USING (inventory_id)
            JOIN payment USING (rental_id)
            GROUP BY actor_id
        ),
        total_values_of_all_least_rented_film_actors AS
        (
            SELECT SUM(values_of_all_least_rented_film_actors) 
                      AS total_value_of_all_least_rented_film_actors
            FROM values_of_all_actors_of_least_rented_films
        ),
        total_values_of_most_popular_actors_of_most_rented_films AS
        (
            SELECT SUM(values_of_most_popular_most_rented_film_actors) 
                       AS total_value_of_most_popular_most_rented_film_actors
            FROM values_of_most_popular_actors_of_most_rented_films
        )
    -- SELECT * FROM film_rental_counts
    -- SELECT * FROM min_max_rental_counts
    -- SELECT * FROM least_rented_films
    -- SELECT * FROM most_rented_films
    -- SELECT * FROM actors_of_least_rented_films
    -- SELECT * FROM actors_of_most_rented_films
    -- SELECT * FROM film_counts_of_actors_of_most_rented_films
    -- SELECT * FROM most_popular_actors_of_most_rented_films
    -- SELECT * FROM all_films_of_most_popular_actors_of_most_rented_films
    -- SELECT * FROM values_of_all_actors_of_least_rented_films ORDER BY actor_id
    -- SELECT * FROM total_values_of_all_least_rented_film_actors
    SELECT * FROM total_values_of_most_popular_actors_of_most_rented_films
    """
)

#### Comparison of the two total values.

In [ ]:
df_query(conn,
    """
    WITH
		film_rental_counts AS
		(
            SELECT film_id,
            	   COUNT(rental_id) AS rental_count
            FROM film
            JOIN inventory USING (film_id)
            JOIN rental USING (inventory_id)
            GROUP BY film_id
            ORDER BY rental_count
    	),
        min_max_rental_counts AS
        (
    		SELECT MIN(rental_count) AS min_rental_count,
                   MAX(rental_count) AS max_rental_count
            FROM film_rental_counts
        ),
        least_rented_films AS
        (
            SELECT rental_count,
                   film_id AS least_rented_film_id
            FROM film_rental_counts
            JOIN min_max_rental_counts
            WHERE rental_count = min_rental_count
        ),
        most_rented_films AS
        (
            SELECT rental_count,
                   film_id AS most_rented_film_id
            FROM film_rental_counts
            JOIN min_max_rental_counts
            WHERE rental_count = max_rental_count
        ),
        actors_of_least_rented_films AS
        (
            SELECT DISTINCT actor_id
            FROM film_actor 
            JOIN least_rented_films
            WHERE film_id = least_rented_film_id
        ),
        actors_of_most_rented_films AS
        (
            SELECT DISTINCT actor_id
            FROM film_actor 
            JOIN most_rented_films
            WHERE film_id = most_rented_film_id
        ),
        film_counts_of_actors_of_most_rented_films AS
        (
            SELECT actor_id, 
                   COUNT(film_id) AS film_count
            FROM actors_of_most_rented_films
            JOIN film_actor USING (actor_id)
            GROUP BY actor_id
            ORDER BY film_count DESC
        ),
        most_popular_actors_of_most_rented_films AS
        (
            SELECT actor_id
            FROM film_counts_of_actors_of_most_rented_films
            WHERE film_count = (
                SELECT MAX(film_count)
                FROM film_counts_of_actors_of_most_rented_films
            )
        ),
        all_films_of_most_popular_actors_of_most_rented_films AS
        (
            SELECT actor_id, film_id
            FROM most_popular_actors_of_most_rented_films
            JOIN film_actor USING (actor_id)
        ),
        values_of_all_actors_of_least_rented_films AS
        (
            SELECT actor_id, 
                   SUM(amount) AS values_of_all_least_rented_film_actors
            FROM actors_of_least_rented_films
            JOIN film_actor USING (actor_id)
            JOIN film USING (film_id)
            JOIN inventory USING (film_id)
            JOIN rental USING (inventory_id)
            JOIN payment USING (rental_id)
            GROUP BY actor_id
        ),
        values_of_most_popular_actors_of_most_rented_films AS
        (
            SELECT actor_id,
                   SUM(amount) AS values_of_most_popular_most_rented_film_actors
            FROM most_popular_actors_of_most_rented_films
            JOIN film_actor USING (actor_id)
            JOIN film USING (film_id)
            JOIN inventory USING (film_id)
            JOIN rental USING (inventory_id)
            JOIN payment USING (rental_id)
            GROUP BY actor_id
        ),
        total_values_of_all_least_rented_film_actors AS
        (
            SELECT SUM(values_of_all_least_rented_film_actors) 
                      AS total_value_of_all_least_rented_film_actors
            FROM values_of_all_actors_of_least_rented_films
        ),
        total_values_of_most_popular_actors_of_most_rented_films AS
        (
            SELECT SUM(values_of_most_popular_most_rented_film_actors) 
                       AS total_value_of_most_popular_most_rented_film_actors
            FROM values_of_most_popular_actors_of_most_rented_films
        ),
        comparison_of_values AS
        (
            SELECT CONCAT('$', FORMAT(total_value_of_all_least_rented_film_actors, 2))
                        AS 'Total value of all actors of the least rented films',
                   CONCAT('$', FORMAT(total_value_of_most_popular_most_rented_film_actors, 2))
                        AS 'Total value of the most popular actors of the most rented films'     
            FROM total_values_of_all_least_rented_film_actors
            JOIN total_values_of_most_popular_actors_of_most_rented_films
        )
    -- SELECT * FROM film_rental_counts
    -- SELECT * FROM min_max_rental_counts
    -- SELECT * FROM least_rented_films
    -- SELECT * FROM most_rented_films
    -- SELECT * FROM actors_of_least_rented_films
    -- SELECT * FROM actors_of_most_rented_films
    -- SELECT * FROM film_counts_of_actors_of_most_rented_films
    -- SELECT * FROM most_popular_actors_of_most_rented_films
    -- SELECT * FROM all_films_of_most_popular_actors_of_most_rented_films
    -- SELECT * FROM values_of_all_actors_of_least_rented_films ORDER BY actor_id
    -- SELECT * FROM total_values_of_all_least_rented_film_actors
    -- SELECT * FROM total_values_of_most_popular_actors_of_most_rented_films
    SELECT * FROM comparison_of_values
    """
)

In [ ]:
conn.close()